<h1 style="text-align: center;"> Fortune Finders: the living wage expedition </h1>
<h2 style="text-align: center;"> Empowering workers with concrete data to support fair salary negotiations.</h2>

<h3> Introduction </h3>

To achieve the goal specified above this notebook will utilize and cross examine, the data tables<br/>  from the MIT Living Wage Calculator with Census and BEA data. We will compare typical salaries<br/> by industry and state (adjusted for price parity) with living wage data to anwer the following questions: 
1. Which regions (state, county, Metro-city) offers the best salary-to-living-wage ratio for a typical industry?
1. How do do the ratios vary between geographic locations and occupations?

<a id = "toc"></a>
### Table of Contents
- [Imports and Raw Data Preview](#Topic0)
    - [Imports](#Topic01)
    - [Raw Data Preview](#Topic02)
- [MIT Data with Population](#Topic1)
    - [Census Population Data Clean and Prep](#Topic11)
    - [MIT Tables Merged With Census Populations](#Topic12)
- [MIT Data State Summaries](#Topic2)

<a id = "Topic0"></a> 

### Imports and Raw Data Preview
#### Imports

In [1]:
# version = 3.11.4

import warnings
warnings.filterwarnings("ignore", category = DeprecationWarning)
warnings.filterwarnings("ignore", category = FutureWarning)

import pandas as pd
from IPython.display import display, Markdown
import numpy as np
from numpy.random import randint
import geopandas as gpd
import matplotlib.pyplot as plt
import json
import altair as alt
alt.data_transformers.enable("vegafusion")
from matplotlib import gridspec

# Set up choropleth map
geojson_path = 'data/ne_110m_admin_1_states_provinces.shp'
states = gpd.read_file(geojson_path)
states = states.to_crs("EPSG:3395")


In [2]:
#BEA Data brought in here as csv to protect our API key
RPP = pd.read_csv('price_parities.csv') #BEA Price parities: SARPP Table
StateSalary = pd.read_csv('personal_income.csv') #Average State Salary: SAINC5N Report
SSRPP = pd.read_csv('combined.csv') #Average State Salary adjusted by RPP

#MIT Living Wage Data
CostDF = pd.read_csv('createdassets/CostDF.csv')
SalaryDF = pd.read_csv('createdassets/SalaryDF.csv')
WageDF = pd.read_csv('createdassets/WageDF.csv')

for d in [CostDF, SalaryDF, WageDF]:
    d.drop(['Unnamed: 0'], axis=1,inplace=True)

#Census Data CountyPopUSCensus or CPUC
 
CPUC = pd.read_excel(
    'createdassets/CensusData/co-est2022-pop.xlsx',
    header = [3],
    skiprows = [4,326,3149,3150,3151,3152,3153]    
    #4: total of whole of united states
    #326: District of Columbia
    #3149-3153: Table footnotes captured below
)
CPUC.columns = ['Geographic Area', 'April 1, 2020 Estimates Base', 'Population Estimate 2020', 'Population Estimate 2021', 'Population Estimate 2022']

<a id='Topic02'></a> 
#### Raw Data Preview
<a href='#toc'>TOC</a>

In [3]:
Tables = {
    "2022 Price Parities": RPP,
    "2022 Average State Salary": StateSalary,
    "Average State Salary adjusted by RPP":SSRPP,
    "MIT Living Wage: Wages by County":WageDF,
    "MIT Living Wage: Typical Expenses by County":CostDF,
    "MIT Living Wage: Occupation Salary by County":SalaryDF,
    "County Population US Census":CPUC
    }

for title, table in Tables.items():
    display(Markdown('<br/><h5>{}</h5>'.format(title)))

    rows = 5
    if "Wages" in title:
        rows = 3
    if "Expenses" in title:
        rows = 10
    if "Occupation" in title:
        rows =  22
    display(table.head(rows))

<br/><h5>2022 Price Parities</h5>

Code  GeoFips        GeoName  TimePeriod CL_UNIT  UNIT_MULT  DataValue
0  SARPP-1        0  United States        2022   Index          0    100.000
1  SARPP-1     1000        Alabama        2022   Index          0     87.776
2  SARPP-1     2000         Alaska        2022   Index          0    101.989
3  SARPP-1     4000        Arizona        2022   Index          0     99.897
4  SARPP-1     5000       Arkansas        2022   Index          0     86.597

<br/><h5>2022 Average State Salary</h5>

Code  GeoFips        GeoName  TimePeriod  CL_UNIT  UNIT_MULT  \
0  SAINC5N-30        0  United States        2022  Dollars          0   
1  SAINC5N-30     1000        Alabama        2022  Dollars          0   
2  SAINC5N-30     2000         Alaska        2022  Dollars          0   
3  SAINC5N-30     4000        Arizona        2022  Dollars          0   
4  SAINC5N-30     5000       Arkansas        2022  Dollars          0   

   DataValue  NoteRef  
0      65470        3  
1      50916        3  
2      68635        3  
3      58442        3  
4      52618        3

<br/><h5>Average State Salary adjusted by RPP</h5>

...

CostType 1 ADULT - 0 1 ADULT - 1 1 ADULT - 2  \
0                                 Food     $3,351      $4,937      $7,417    
1                           Child Care         $0      $6,261     $12,521    
2                              Medical     $2,733      $7,921      $7,708    
3                              Housing     $8,310     $11,789     $11,789    
4                       Transportation     $5,509      $9,776     $12,709    
5                                Civic     $2,503      $4,019      $4,965    
6                                Other     $4,508      $6,723      $6,150    
7   Required annual income after taxes    $27,036     $51,550     $63,383    
8                         Annual taxes     $6,321     $12,053     $14,819    
9  Required annual income before taxes    $33,357     $63,602     $78,203    

  1 ADULT - 3 2 ADULTS(1 WORKING) - 0 2 ADULTS(1 WORKING) - 1  \
0     $9,838                  $6,143                  $7,645    
1    $18,782                      $0                      $0    
2     $8,018                  $6,298                  $7,708    
3    $14,906                  $9,946                 $11,789    
4    $15,012                  $9,776                 $12,709    
5     $6,483                  $4,019                  $4,965    
6     $8,948                  $6,723                  $6,150    
7    $82,110                 $43,027                 $51,090    
8    $19,198                 $10,060                 $11,945    
9   $101,308                 $53,087                 $63,035    

  2 ADULTS(1 WORKING) - 2 2 ADULTS(1 WORKING) - 3 2 ADULTS(BOTH WORKING) - 0  \
0                 $9,856                 $11,999                     $6,143    
1                     $0                      $0                         $0    
2                 $8,018                  $7,807                     $6,298    
3                $11,789                 $14,906                     $9,946    
4                $15,012                 $16,304                     $9,776    
5                 $6,483                  $5,153                     $4,019    
6                 $8,948                  $8,655                     $6,723    
7                $60,230                 $64,946                    $43,027    
8                $14,082                 $15,185                    $10,060    
9                $74,312                 $80,131                    $53,087    

  2 ADULTS(BOTH WORKING) - 1 2 ADULTS(BOTH WORKING) - 2  \
0                    $7,645                     $9,856    
1                    $6,261                    $12,521    
2                    $7,708                     $8,018    
3                   $11,789                    $11,789    
4                   $12,709                    $15,012    
5                    $4,965                     $6,483    
6                    $6,150                     $8,948    
7                   $57,351                    $72,751    
8                   $13,409                    $17,010    
9                   $70,760                    $89,760    

  2 ADULTS(BOTH WORKING) - 3    State   County  
0                   $11,999   Alabama  Autauga  
1                   $18,782   Alabama  Autauga  
2                    $7,807   Alabama  Autauga  
3                   $14,906   Alabama  Autauga  
4                   $16,304   Alabama  Autauga  
5                    $5,153   Alabama  Autauga  
6                    $8,655   Alabama  Autauga  
7                   $83,728   Alabama  Autauga  
8                   $19,576   Alabama  Autauga  
9                  $103,304   Alabama  Autauga

<br/><h5>MIT Living Wage: Occupation Salary by County</h5>

Occupational Area Typical Annual Salary  \
0                                          Management             $101,778    
1                 Business &amp; Financial Operations              $71,198    
2                         Computer &amp; Mathematical              $86,938    
3                      Architecture &amp; Engineering              $90,447    
4                Life, Physical, &amp; Social Science              $64,992    
5                      Community &amp; Social Service              $47,059    
6                                               Legal              $69,240    
7                  Education, Training, &amp; Library              $54,260    
8    Arts, Design, Entertainment, Sports, &amp; Media              $41,698    
9            Healthcare Practitioners &amp; Technical              $58,080    
10                                 Healthcare Support              $26,055    
11                                 Protective Service              $39,975    
12             Food Preparation &amp; Serving Related              $20,812    
13  Building &amp; Grounds Cleaning &amp; Maintenance              $26,108    
14                        Personal Care &amp; Service              $23,925    
15                                Sales &amp; Related              $28,291    
16                Office &amp; Administrative Support              $36,829    
17                   Farming, Fishing, &amp; Forestry              $32,132    
18                      Construction &amp; Extraction              $42,490    
19            Installation, Maintenance, &amp; Repair              $48,910    
20                                         Production              $36,123    
21               Transportation &amp; Material Moving              $32,175    

      State   County  
0   Alabama  Autauga  
1   Alabama  Autauga  
2   Alabama  Autauga  
3   Alabama  Autauga  
4   Alabama  Autauga  
5   Alabama  Autauga  
6   Alabama  Autauga  
7   Alabama  Autauga  
8   Alabama  Autauga  
9   Alabama  Autauga  
10  Alabama  Autauga  
11  Alabama  Autauga  
12  Alabama  Autauga  
13  Alabama  Autauga  
14  Alabama  Autauga  
15  Alabama  Autauga  
16  Alabama  Autauga  
17  Alabama  Autauga  
18  Alabama  Autauga  
19  Alabama  Autauga  
20  Alabama  Autauga  
21  Alabama  Autauga

<br/><h5>County Population US Census</h5>

Geographic Area  April 1, 2020 Estimates Base  \
0  .Autauga County, Alabama                         58802   
1  .Baldwin County, Alabama                        231761   
2  .Barbour County, Alabama                         25224   
3     .Bibb County, Alabama                         22300   
4   .Blount County, Alabama                         59130   

   Population Estimate 2020  Population Estimate 2021  \
0                     58902                     59210   
1                    233219                    239361   
2                     24960                     24539   
3                     22183                     22370   
4                     59102                     59085   

   Population Estimate 2022  
0                     59759  
1                    246435  
2                     24706  
3                     22005  
4                     59512

<a id = "Topic1"></a>

### MIT Data with Population
#### Add county populations
*Population via Census merged to MIT Tables:
Cost, Salary and Wage tables from the MIT Living Wage Data set will be combined with county population via Census

<a id = "Topic11"></a>

#### Clean up CPUC for merge
1. define split function
2. split data
3. check for missing rows between MIT data and Census
4. examine  differences, revisit and modify step 2 until all MIT rows match
5. Inner merge MIT Table and CPUC Tables

<a href='#toc'>TOC</a>

In [4]:
# Function to split the 'Geographic Area'[column in CPUC] into 'County' and 'State'
def split_geographic_area(area):
    
    area_cleaned = area.strip('.').strip() # Strip leading periods and whitespace    
    parts = area_cleaned.split(',') # Most pairs have format [County equivalent],[state]
    
    # If there's no comma or an unexpected format, return placeholders indicating a need for manual review
    if len(parts) != 2:
        return ['Invalid Format - Review Needed', 'Invalid Format - Review Needed']
    # Trim whitespace from parts to ensure clean data
    county, state = parts[0].strip(), parts[1].strip()
    return county, state

In [5]:
CPUC_1 = CPUC.copy() #maintain original 

#split the 'Geographic Area' into 'County' and 'State'
CPUC_1[['County Equivalent', 'State']] = CPUC_1.apply(lambda row: split_geographic_area(row['Geographic Area']), axis=1, result_type='expand')
#merge destination has the word "County stripped from county entries (although maintains other title like "Parish")"
CPUC_1['County Equivalent'] = CPUC_1['County Equivalent'].str.replace(' County', '', regex=False) 
CPUC_1['County Equivalent'] = CPUC_1['County Equivalent'].str.replace(' Borough', '', regex=False) 
CPUC_1['County Equivalent'] = CPUC_1['County Equivalent'].str.replace(' Census Area', '', regex=False)
CPUC_1['County Equivalent'] = CPUC_1['County Equivalent'].str.replace(' Parish', '', regex=False) 
CPUC_1['County Equivalent'] = CPUC_1['County Equivalent'].str.replace(' Planning Region', '', regex=False)

#Connecticut uses regions instead of counties we'll approximately correct for this
CT_rename_map={
    "Northwest Hills": "Litchfield",
    "Naugatuck Valley": "New Haven",
    "South Central Connecticut": "New Haven",
    "Western Connecticut": "Fairfield",
    "Greater Bridgeport": "Fairfield",
    "Lower Connecticut River Valley": "Middlesex",
    "Southeastern Connecticut": "New London",
    "Northeastern Connecticut": "Windham"
}

for old_name, new_name in CT_rename_map.items():
    CPUC_1.loc[(CPUC_1['State'] == 'Connecticut') & (CPUC_1['County Equivalent'].str.contains(old_name, case=False)), 'County Equivalent'] = new_name

# Connecticut census combines Tolland and Haartford counties. I'm going to drop capitol and manualy add them
CPUC_1 = CPUC_1[~((CPUC_1['County Equivalent'] == 'Capitol') & (CPUC_1['State'] == 'Connecticut'))]

# Add new entries for Hartford and Tolland
new_rows = pd.DataFrame([
    [".Hartford County, Connecticut", 897932, 897932, 898636, 898636, "Hartford", "Connecticut"],
    [".Tolland County, Connecticut", 149650, 149650, 150293, 150120, "Tolland", "Connecticut"]
], columns=['Geographic Area', 'April 1, 2020 Estimates Base', 'Population Estimate 2020', 'Population Estimate 2021', 'Population Estimate 2022', 'County Equivalent', 'State'])

CPUC_1 = pd.concat([CPUC_1, new_rows], ignore_index=True)

#Alaska corrections
AK_rename_map={
    "Anchorage Municipality": "Valdez-Cordova",
    "Chugach": "Valdez-Cordova",
    "Copper River": "Valdez-Cordova"
} 

for old_name, new_name in AK_rename_map.items():
    CPUC_1.loc[(CPUC_1['State'] == 'Alaska') & (CPUC_1['County Equivalent'].str.contains(old_name, case=False)), 'County Equivalent'] = new_name


#Virginia Corrections
VI_rename_map={
    "Alexandria city" : "Alexandria",
    "Bristol city" : "Bristol",
    "Buena Vista city" : "Buena Vista",
    "Charlottesville city" : "Charlottesville",
    "Chesapeake city" : "Chesapeake",
    "Colonial Heights city" : "Colonial Heights",
    "Covington city" : "Covington",
    "Danville city" : "Danville",
    "Emporia city" : "Emporia",
    "Falls Church city" : "Falls Church",
    "Fredericksburg city" : "Fredericksburg",
    "Galax city" : "Galax",
    "Hampton city" : "Hampton",
    "Harrisonburg city" : "Harrisonburg",
    "Hopewell city" : "Hopewell",
    "Lexington city" : "Lexington",
    "Lynchburg city" : "Lynchburg",
    "Manassas Park city" : "Manassas Park",
    "Manassas city" : "Manassas",
    "Martinsville city" : "Martinsville",
    "Newport News city" : "Newport News",
    "Norfolk city" : "Norfolk",
    "Norton city" : "Norton",
    "Petersburg city" : "Petersburg",
    "Radford city" : "Poquoson",
    "Richmond city" : "Portsmouth",
    "Roanoke city" : "Radford",
    "Salem city" : "Salem",
    "Staunton city" : "Staunton",
    "Suffolk city" : "Suffolk",
    "Virginia Beach city" : "Virginia Beach",
    "Waynesboro city" : "Waynesboro",
    "Williamsburg city" : "Williamsburg",
    "Winchester city" : "Winchester"
}

for old_name, new_name in VI_rename_map.items():
    CPUC_1.loc[(CPUC_1['State'] == 'Virginia') & (CPUC_1['County Equivalent'].str.contains(old_name, case=False)), 'County Equivalent'] = new_name


#duplicates now exist form some counties lets aggregate
aggregated_df = CPUC_1.groupby(['County Equivalent', 'State']).agg({
    'April 1, 2020 Estimates Base': 'sum',
    'Population Estimate 2020': 'sum',
    'Population Estimate 2021': 'sum',
    'Population Estimate 2022': 'sum'
}).reset_index()
aggregated_df['Geographic Area'] = aggregated_df['County Equivalent'] + " , " + aggregated_df['State']
aggregated_df = aggregated_df[['Geographic Area', 'April 1, 2020 Estimates Base', 'Population Estimate 2020', 'Population Estimate 2021', 'Population Estimate 2022', 'County Equivalent', 'State']]
CPUC_1 = aggregated_df



CPUC_1_Invalid = len( CPUC_1[CPUC_1['County Equivalent'] == 'Invalid Format - Review Needed' ])
CPUC_1_Valid = len(CPUC) - CPUC_1_Invalid

print(f'Number of total counties: {len(CPUC_1)}')
print(f'Number of valid county-state splits: {CPUC_1_Valid}')
print(f'Number of invalid county-state splits: {CPUC_1_Invalid}')

CPUC_1.head(20)

Number of total counties: 3140
Number of valid county-state splits: 3143
Number of invalid county-state splits: 0


Geographic Area  April 1, 2020 Estimates Base  \
0   Abbeville , South Carolina                         24287   
1           Acadia , Louisiana                         57569   
2          Accomack , Virginia                         33417   
3                  Ada , Idaho                        494964   
4                 Adair , Iowa                          7498   
5             Adair , Kentucky                         18903   
6             Adair , Missouri                         25315   
7             Adair , Oklahoma                         19494   
8             Adams , Colorado                        519582   
9                Adams , Idaho                          4380   
10            Adams , Illinois                         65727   
11             Adams , Indiana                         35811   
12                Adams , Iowa                          3708   
13         Adams , Mississippi                         29538   
14            Adams , Nebraska                         31202   
15        Adams , North Dakota                          2200   
16                Adams , Ohio                         27474   
17        Adams , Pennsylvania                        103829   
18          Adams , Washington                         20612   
19           Adams , Wisconsin                         20646   

    Population Estimate 2020  Population Estimate 2021  \
0                      24256                     24258   
1                      57472                     57262   
2                      33388                     33364   
3                     498260                    512914   
4                       7494                      7538   
5                      18880                     18953   
6                      25269                     25179   
7                      19451                     19479   
8                     520479                    523592   
9                       4425                      4632   
10                     65612                     65146   
11                     35852                     35939   
12                      3710                      3642   
13                     29419                     28804   
14                     31177                     30990   
15                      2187                      2152   
16                     27440                     27513   
17                    103779                    105632   
18                     20608                     20640   
19                     20675                     20795   

    Population Estimate 2022 County Equivalent           State  
0                      24356         Abbeville  South Carolina  
1                      56744            Acadia       Louisiana  
2                      33191          Accomack        Virginia  
3                     518907               Ada           Idaho  
4                       7494             Adair            Iowa  
5                      19067             Adair        Kentucky  
6                      25165             Adair        Missouri  
7                      19576             Adair        Oklahoma  
8                     527575             Adams        Colorado  
9                       4817             Adams           Idaho  
10                     64725             Adams        Illinois  
11                     36068             Adams         Indiana  
12                      3611             Adams            Iowa  
13                     28408             Adams     Mississippi  
14                     30970             Adams        Nebraska  
15                      2115             Adams    North Dakota  
16                     27420             Adams            Ohio  
17                    106027             Adams    Pennsylvania  
18                     20961             Adams      Washington  
19                     21226             Adams       Wisconsin

In [6]:
# we will merge several dfs on state and county
# lets examine thier sizes 
print(f'WageDF has {len(WageDF[["County", "State"]].copy().drop_duplicates())} counties')
print(f'CostDF has {len(CostDF[["County", "State"]].copy().drop_duplicates())} counties')
print(f'SalaryDF has {len(SalaryDF[["County", "State"]].copy().drop_duplicates())} counties')


WageDF has 3115 counties
CostDF has 3115 counties
SalaryDF has 3115 counties


In [7]:
# lets examine missing pairings
# Create unique state-county identifiers for each dataset
WageDF['State-County'] = WageDF['State'] + '-' + WageDF['County']
CPUC_1['State-County'] = CPUC_1['State'] + '-' + CPUC_1['County Equivalent']

wage_unique_pairings = set(WageDF['State-County'])
census_unique_pairings = set(CPUC_1['State-County'])
merged_unique_pairings = set(WageDF['State'] + '-' + WageDF['County']) & set(CPUC_1['State'] + '-' + CPUC_1['County Equivalent'])

# Identify missing pairings in merged_df from both wage_df and census_df_cleaned
missing_in_merged_from_wage = wage_unique_pairings - merged_unique_pairings
missing_in_merged_from_census = census_unique_pairings - merged_unique_pairings

# Filter wage_df and census_df_cleaned for the missing pairings
missing_rows_wage_df = WageDF[WageDF['State-County'].isin(missing_in_merged_from_wage)]
missing_rows_census_df_cleaned = CPUC_1[CPUC_1['State-County'].isin(missing_in_merged_from_census)]



#Display the count of missing rows for each dataset to understand the scope
M_MIT = missing_rows_wage_df[["County", "State"]].copy().drop_duplicates()
M_CPUC = missing_rows_census_df_cleaned[["County Equivalent", "State"]].copy().drop_duplicates()

#from here we'll compare and loop back to and modify CPUC_1 definition until all counties from wage_df are matched
display(Markdown('<br/><h5>{}: {}</h5>'.format("Unmatched MIT counties", len(M_MIT))))
display(M_MIT.head(30))
display(Markdown('<br/><h5>{}: {}</h5>'.format("Unmatched Census counties", len(M_CPUC))))
display(M_CPUC.head(30))

<br/><h5>Unmatched MIT counties: 0</h5>

Empty DataFrame
Columns: [County, State]
Index: []

<br/><h5>Unmatched Census counties: 25</h5>

County Equivalent         State
122         Baltimore city      Maryland
271                Bristol  Rhode Island
815               Doña Ana    New Mexico
840                 Echols       Georgia
895           Fairfax city      Virginia
976          Franklin city      Virginia
1073            Grand Isle       Vermont
1383            James City      Virginia
1457       Juneau City and        Alaska
1460               Kalawao        Hawaii
1543               LaSalle      Illinois
1544               LaSalle     Louisiana
1665               Lincoln         Maine
2236            Petersburg        Alaska
2273           Piscataquis         Maine
2311         Poquoson city      Virginia
2316       Portsmouth city      Virginia
2367               Quitman       Georgia
2615        Sitka City and        Alaska
2617  Skagway Municipality        Alaska
2629              Somerset         Maine
2664        St. Louis city      Missouri
3006               Webster       Georgia
3102     Wrangell City and        Alaska
3114      Yakutat City and        Alaska

Our dataset is missing some counties and we're unable to reconcile them. The original MIT data for this analysis came from a data pull in May 2022. Since that pull it has been noticed on the MIT Living Wage Calculator website that they request no web scrapping. We submitted a request to thier API but haven't heard back likely due to the fact they update thier tables yearly in January. As such we will use the data we have and respect thier wishes. The data is still public and could be grabbed table by table without the API via copy paste. So we press on to merge the data

<a name = "Topic12"></a>

### MIT Data With Population Tables

<a href='#toc'>TOC</a>

In [8]:
CPUC_1 = CPUC_1[["Population Estimate 2022","County Equivalent", "State"]]

WageDFwithPop = pd.merge(CPUC_1, WageDF, left_on=['State', 'County Equivalent'], right_on=['State', 'County'], how='inner')
CostDFwithPop = pd.merge(CPUC_1, CostDF, left_on=['State', 'County Equivalent'], right_on=['State', 'County'], how='inner')
SalaryDFwithPop = pd.merge(CPUC_1, SalaryDF, left_on=['State', 'County Equivalent'], right_on=['State', 'County'], how='inner')


display(Markdown('<br/><h5>{}</h5>'.format("MIT Living Wage: Wages by County and Population")))
display(WageDFwithPop.head(3))
display(Markdown('<br/><h5>{}</h5>'.format("MIT Living Wage: Typical Expenses by County and Population")))
display(CostDFwithPop.head(10))
display(Markdown('<br/><h5>{}</h5>'.format("MIT Living Wage: Occupation Salary by County and Population")))
display(SalaryDFwithPop.head(22))



<br/><h5>MIT Living Wage: Wages by County and Population</h5>

Population Estimate 2022 County Equivalent           State      WageType  \
0                     24356         Abbeville  South Carolina   Living Wage   
1                     24356         Abbeville  South Carolina  Poverty Wage   
2                     24356         Abbeville  South Carolina  Minimum Wage   

  1 ADULT - 0 1 ADULT - 1 1 ADULT - 2 1 ADULT - 3 2 ADULTS(1 WORKING) - 0  \
0     $15.57      $29.48      $35.86      $46.84                  $24.67    
1      $6.19       $8.38      $10.56      $12.74                   $8.38    
2      $7.25       $7.25       $7.25       $7.25                   $7.25    

  2 ADULTS(1 WORKING) - 1 2 ADULTS(1 WORKING) - 2 2 ADULTS(1 WORKING) - 3  \
0                 $30.03                  $35.59                  $38.88    
1                 $10.56                  $12.74                  $14.92    
2                  $7.25                   $7.25                   $7.25    

  2 ADULTS(BOTH WORKING) - 0 2 ADULTS(BOTH WORKING) - 1  \
0                    $12.33                     $16.51    
1                     $4.19                      $5.28    
2                     $7.25                      $7.25    

  2 ADULTS(BOTH WORKING) - 2 2 ADULTS(BOTH WORKING) - 3     County  \
0                    $20.78                     $23.91   Abbeville   
1                     $6.37                      $7.46   Abbeville   
2                     $7.25                      $7.25   Abbeville   

               State-County  
0  South Carolina-Abbeville  
1  South Carolina-Abbeville  
2  South Carolina-Abbeville

<br/><h5>MIT Living Wage: Typical Expenses by County and Population</h5>

Population Estimate 2022 County Equivalent           State  \
0                     24356         Abbeville  South Carolina   
1                     24356         Abbeville  South Carolina   
2                     24356         Abbeville  South Carolina   
3                     24356         Abbeville  South Carolina   
4                     24356         Abbeville  South Carolina   
5                     24356         Abbeville  South Carolina   
6                     24356         Abbeville  South Carolina   
7                     24356         Abbeville  South Carolina   
8                     24356         Abbeville  South Carolina   
9                     24356         Abbeville  South Carolina   

                              CostType 1 ADULT - 0 1 ADULT - 1 1 ADULT - 2  \
0                                 Food     $3,351      $4,937      $7,417    
1                           Child Care         $0      $4,903      $9,805    
2                              Medical     $2,957      $9,182      $8,969    
3                              Housing     $6,648      $8,816      $8,816    
4                       Transportation     $5,509      $9,776     $12,709    
5                                Civic     $2,503      $4,019      $4,965    
6                                Other     $4,508      $6,723      $6,150    
7   Required annual income after taxes    $25,599     $48,479     $58,955    
8                         Annual taxes     $6,784     $12,848     $15,624    
9  Required annual income before taxes    $32,383     $61,327     $74,579    

  1 ADULT - 3 2 ADULTS(1 WORKING) - 0 2 ADULTS(1 WORKING) - 1  \
0     $9,838                  $6,143                  $7,645    
1    $14,708                      $0                      $0    
2     $9,278                  $7,086                  $8,969    
3    $12,620                  $6,687                  $8,816    
4    $15,012                  $9,776                 $12,709    
5     $6,483                  $4,019                  $4,965    
6     $8,948                  $6,723                  $6,150    
7    $77,011                 $40,556                 $49,377    
8    $20,410                 $10,748                 $13,086    
9    $97,421                 $51,304                 $62,463    

  2 ADULTS(1 WORKING) - 2 2 ADULTS(1 WORKING) - 3 2 ADULTS(BOTH WORKING) - 0  \
0                 $9,856                 $11,999                     $6,143    
1                     $0                      $0                         $0    
2                 $9,278                  $9,067                     $7,086    
3                 $8,816                 $12,620                     $6,687    
4                $15,012                 $16,304                     $9,776    
5                 $6,483                  $5,153                     $4,019    
6                 $8,948                  $8,655                     $6,723    
7                $58,517                 $63,922                    $40,556    
8                $15,508                 $16,941                    $10,748    
9                $74,025                 $80,862                    $51,304    

  2 ADULTS(BOTH WORKING) - 1 2 ADULTS(BOTH WORKING) - 2  \
0                    $7,645                     $9,856    
1                    $4,903                     $9,805    
2                    $8,969                     $9,278    
3                    $8,816                     $8,816    
4                   $12,709                    $15,012    
5                    $4,965                     $6,483    
6                    $6,150                     $8,948    
7                   $54,280                    $68,322    
8                   $14,385                    $18,107    
9                   $68,666                    $86,429    

  2 ADULTS(BOTH WORKING) - 3     County  
0                   $11,999   Abbeville  
1                   $14,708   Abbeville  
2                    $9,067   Abbeville  
3            

<br/><h5>MIT Living Wage: Occupation Salary by County and Population</h5>

Population Estimate 2022 County Equivalent           State  \
0                      24356         Abbeville  South Carolina   
1                      24356         Abbeville  South Carolina   
2                      24356         Abbeville  South Carolina   
3                      24356         Abbeville  South Carolina   
4                      24356         Abbeville  South Carolina   
5                      24356         Abbeville  South Carolina   
6                      24356         Abbeville  South Carolina   
7                      24356         Abbeville  South Carolina   
8                      24356         Abbeville  South Carolina   
9                      24356         Abbeville  South Carolina   
10                     24356         Abbeville  South Carolina   
11                     24356         Abbeville  South Carolina   
12                     24356         Abbeville  South Carolina   
13                     24356         Abbeville  South Carolina   
14                     24356         Abbeville  South Carolina   
15                     24356         Abbeville  South Carolina   
16                     24356         Abbeville  South Carolina   
17                     24356         Abbeville  South Carolina   
18                     24356         Abbeville  South Carolina   
19                     24356         Abbeville  South Carolina   
20                     24356         Abbeville  South Carolina   
21                     24356         Abbeville  South Carolina   

                                    Occupational Area Typical Annual Salary  \
0                                          Management             $101,928    
1                 Business &amp; Financial Operations              $67,464    
2                         Computer &amp; Mathematical              $77,329    
3                      Architecture &amp; Engineering              $80,999    
4                Life, Physical, &amp; Social Science              $64,457    
5                      Community &amp; Social Service              $42,212    
6                                               Legal              $62,777    
7                  Education, Training, &amp; Library              $49,958    
8    Arts, Design, Entertainment, Sports, &amp; Media              $45,250    
9            Healthcare Practitioners &amp; Technical              $65,891    
10                                 Healthcare Support              $28,869    
11                                 Protective Service              $39,098    
12             Food Preparation &amp; Serving Related              $21,764    
13  Building &amp; Grounds Cleaning &amp; Maintenance              $26,836    
14                        Personal Care &amp; Service              $26,055    
15                                Sales &amp; Related              $28,847    
16                Office &amp; Administrative Support              $37,611    
17                   Farming, Fishing, &amp; Forestry              $31,833    
18                      Construction &amp; Extraction              $42,757    
19            Installation, Maintenance, &amp; Repair              $47,776    
20                                         Production              $39,847    
21               Transportation &amp; Material Moving              $32,624    

       County  
0   Abbeville  
1   Abbeville  
2   Abbeville  
3   Abbeville  
4   Abbeville  
5   Abbeville  
6   Abbeville  
7   Abbeville  
8   Abbeville  
9   Abbeville  
10  Abbeville  
11  Abbeville  
12  Abbeville  
13  Abbeville  
14  Abbeville  
15  Abbeville  
16  Abbeville  
17  Abbeville  
18  Abbeville  
19  Abbeville  
20  Abbeville  
21  Abbeville

<a id = Topic2></a>

### MIT Data State Summaries
#### County data Projected up to state level
*weighting projection by county population

<a href='#toc'>TOC</a>

#### State Data Aggregation for cost and wage

In [9]:
CostDFwithPop = CostDFwithPop[['Population Estimate 2022', 'State', 'CostType', 'County','1 ADULT - 0', '1 ADULT - 1', '1 ADULT - 2', '1 ADULT - 3',
       '2 ADULTS(1 WORKING) - 0', '2 ADULTS(1 WORKING) - 1',
       '2 ADULTS(1 WORKING) - 2', '2 ADULTS(1 WORKING) - 3',
       '2 ADULTS(BOTH WORKING) - 0', '2 ADULTS(BOTH WORKING) - 1',
       '2 ADULTS(BOTH WORKING) - 2', '2 ADULTS(BOTH WORKING) - 3']]

StateNames = CostDFwithPop['State'].unique()
NewCostDF = pd.DataFrame()

for state in StateNames:
    Dfstate = CostDFwithPop[CostDFwithPop['State'] == state]
    
    # Calculate the total population for the state
    StatePopSum = Dfstate['Population Estimate 2022'].sum()/len(Dfstate['CostType'].unique())
    
    # Initialize an empty DataFrame for the new state data
    NewStateDF = pd.DataFrame(columns=Dfstate.columns.drop(['State', 'County', 'Population Estimate 2022']))
    
    # Aggregate cost data for the state, adjusting by population weight
    for cost_type in Dfstate['CostType'].unique():
        cost_data = Dfstate[Dfstate['CostType'] == cost_type].copy()
        monetary_columns = cost_data.columns[4:]  # Excluding 'Unnamed: 0', 'Population Estimate 2022', 'State', 'CostType', 'County'
        cost_data[monetary_columns] = cost_data[monetary_columns].replace('[\$,]', '', regex=True).astype(float)
        weighted_costs = cost_data[monetary_columns].apply(lambda x: (x * cost_data['Population Estimate 2022']).sum() / StatePopSum, axis=0)
        weighted_costs_dict = weighted_costs.to_dict()
        weighted_costs_dict['CostType'] = cost_type
        assert isinstance(NewStateDF, pd.DataFrame), "NewStateDF is not a DataFrame"
        NewStateDF = pd.concat([NewStateDF, pd.DataFrame([weighted_costs_dict])], ignore_index=True)
    
    # Add the state name and population to the aggregated data
    NewStateDF['State'] = state
    NewStateDF['Population Estimate 2022'] = StatePopSum
    
    # Append the processed state data to the new DataFrame
    NewCostDF = pd.concat([NewCostDF, NewStateDF], ignore_index=True)

# Display the first few rows of the aggregated DataFrame to verify the results
StateCostDF = NewCostDF
NewCostDF.head()


CostType  1 ADULT - 0   1 ADULT - 1   1 ADULT - 2   1 ADULT - 3  \
0            Food  3351.000000   4937.000000   7417.000000   9838.000000   
1      Child Care     0.000000   5609.889415  11219.580293  16829.469708   
2         Medical  2957.000000   9182.000000   8969.000000   9278.000000   
3         Housing  9828.407409  12200.552331  12200.552331  15917.694809   
4  Transportation  5509.000000   9776.000000  12709.000000  15012.000000   

   2 ADULTS(1 WORKING) - 0  2 ADULTS(1 WORKING) - 1  2 ADULTS(1 WORKING) - 2  \
0              6143.000000              7645.000000              9856.000000   
1                 0.000000                 0.000000                 0.000000   
2              7086.000000              8969.000000              9278.000000   
3             10451.640438             12200.552331             12200.552331   
4              9776.000000             12709.000000             15012.000000   

   2 ADULTS(1 WORKING) - 3  2 ADULTS(BOTH WORKING) - 0  \
0             11999.000000                 6143.000000   
1                 0.000000                    0.000000   
2              9067.000000                 7086.000000   
3             15917.694809                10451.640438   
4             16304.000000                 9776.000000   

   2 ADULTS(BOTH WORKING) - 1  2 ADULTS(BOTH WORKING) - 2  \
0                 7645.000000                 9856.000000   
1                 5609.889415                11219.580293   
2                 8969.000000                 9278.000000   
3                12200.552331                12200.552331   
4                12709.000000                15012.000000   

   2 ADULTS(BOTH WORKING) - 3           State  Population Estimate 2022  
0                11999.000000  South Carolina                 5282634.0  
1                16829.469708  South Carolina                 5282634.0  
2                 9067.000000  South Carolina                 5282634.0  
3                15917.694809  South Carolina                 5282634.0  
4                16304.000000  South Carolina                 5282634.0

In [10]:
WageDFwithPop = WageDFwithPop[['Population Estimate 2022', 'State', 'WageType', 'County','1 ADULT - 0', '1 ADULT - 1', '1 ADULT - 2', '1 ADULT - 3',
       '2 ADULTS(1 WORKING) - 0', '2 ADULTS(1 WORKING) - 1',
       '2 ADULTS(1 WORKING) - 2', '2 ADULTS(1 WORKING) - 3',
       '2 ADULTS(BOTH WORKING) - 0', '2 ADULTS(BOTH WORKING) - 1',
       '2 ADULTS(BOTH WORKING) - 2', '2 ADULTS(BOTH WORKING) - 3']]
NewWageDF = pd.DataFrame()

# Assuming WageDFwithPop has already had 'County Equivalent' and 'State-County' dropped
StateNames = WageDFwithPop['State'].unique()
NewWageDF = pd.DataFrame()

for state in StateNames:
    Dfstate = WageDFwithPop[WageDFwithPop['State'] == state].copy()
    
    # Calculate the total population for the state
    StatePopSum = Dfstate['Population Estimate 2022'].sum()/len(WageDFwithPop['WageType'].unique())
    
    # Initialize an empty DataFrame for the new state data
    columns_to_keep = Dfstate.columns.drop(['State', 'County', 'Population Estimate 2022'])
    NewStateDF = pd.DataFrame(columns=columns_to_keep)
    
    # Prepare wage data, adjusting by population weight
    for wage_type in Dfstate['WageType'].unique():
        wage_data = Dfstate[Dfstate['WageType'] == wage_type].copy()
        monetary_columns = wage_data.columns[4:]  # Adjust index based on your DataFrame structure
        wage_data[monetary_columns] = wage_data[monetary_columns].replace('[\$,]', '', regex=True).astype(float)
        
        weighted_wages = wage_data[monetary_columns].apply(
            lambda x: (x * wage_data['Population Estimate 2022']).sum() / StatePopSum, axis=0)
        
        weighted_wages_dict = weighted_wages.to_dict()
        weighted_wages_dict['WageType'] = wage_type
        
        NewStateDF = pd.concat([NewStateDF, pd.DataFrame([weighted_wages_dict])], ignore_index=True)
    
    # Add the state name and total population to the aggregated data
    NewStateDF['State'] = state
    NewStateDF['Population Estimate 2022'] = StatePopSum
    
    # Append the processed state data to the new DataFrame
    NewWageDF = pd.concat([NewWageDF, NewStateDF], ignore_index=True)



StateWageDF = NewWageDF
NewWageDF.head()



WageType  1 ADULT - 0  1 ADULT - 1  1 ADULT - 2  1 ADULT - 3  \
0   Living Wage    17.503204    31.971810    38.774883    50.131148   
1  Poverty Wage     6.190000     8.380000    10.560000    12.740000   
2  Minimum Wage     7.250000     7.250000     7.250000     7.250000   
3   Living Wage    16.165557    32.212301    39.759239    51.688243   
4  Poverty Wage     6.190000     8.380000    10.560000    12.740000   

   2 ADULTS(1 WORKING) - 0  2 ADULTS(1 WORKING) - 1  2 ADULTS(1 WORKING) - 2  \
0                26.954471                32.088533                37.648038   
1                 8.380000                10.560000                12.740000   
2                 7.250000                 7.250000                 7.250000   
3                25.820630                31.495922                36.985592   
4                 8.380000                10.560000                12.740000   

   2 ADULTS(1 WORKING) - 3  2 ADULTS(BOTH WORKING) - 0  \
0                40.880712                   13.477657   
1                14.920000                    4.190000   
2                 7.250000                    7.250000   
3                40.059957                   12.911322   
4                14.920000                    4.190000   

   2 ADULTS(BOTH WORKING) - 1  2 ADULTS(BOTH WORKING) - 2  \
0                   17.751381                   22.236004   
1                    5.280000                    6.370000   
2                    7.250000                    7.250000   
3                   17.848505                   22.692651   
4                    5.280000                    6.370000   

   2 ADULTS(BOTH WORKING) - 3           State  Population Estimate 2022  
0                   25.557895  South Carolina                 5282634.0  
1                    7.460000  South Carolina                 5282634.0  
2                    7.250000  South Carolina                 5282634.0  
3                   26.329214       Louisiana                 4575512.0  
4                    7.460000       Louisiana                 4575512.0

#### State Salary Data
One thing we'd come to find out is that salaries arn't estimated by occupation at the county level, instead the statewide estimates are reiteriated for each county. We feel this finding is related to the ethics issues we raised in our proposal. There are some rual counties in the USA where very few individuals work in certain occupations. It's likely the MIT team didn't drill down into county level data here due to privacy concerns. It is possible this data could be aggregated  through a combination of unsupervised and supervised learning combined with BLS statistics however, If the MIT team didn't do it we probably shouldn't either.

In [11]:
StateSalary = SalaryDFwithPop.copy()
StateSalary['Typical Annual Salary'] = StateSalary['Typical Annual Salary'].str.strip().str.replace(',', '').str.replace('$', '').astype(int)
StateSalary.head()
StateSalary = StateSalary.groupby(['State', 'Occupational Area']).agg({'Population Estimate 2022': 'sum', 'Typical Annual Salary': 'sum', 'Typical Annual Salary': lambda x: sum(x * SalaryDFwithPop.loc[x.index, 'Population Estimate 2022']) / sum(SalaryDFwithPop.loc[x.index, 'Population Estimate 2022'])}).reset_index()



#### MIT State Summary Tables

In [12]:

display(Markdown('<br/><h5>{}</h5>'.format("MIT Living Wage: Wages by State and Population")))
display(StateWageDF.head(3))
display(Markdown('<br/><h5>{}</h5>'.format("MIT Living Wage: Typical Expenses by State and Population")))
display(StateCostDF.head(10))
display(Markdown('<br/><h5>{}</h5>'.format("MIT Living Wage: Occupation Salary by State and Population")))
display(StateSalary.head(22))

<br/><h5>MIT Living Wage: Wages by State and Population</h5>

WageType  1 ADULT - 0  1 ADULT - 1  1 ADULT - 2  1 ADULT - 3  \
0   Living Wage    17.503204     31.97181    38.774883    50.131148   
1  Poverty Wage     6.190000      8.38000    10.560000    12.740000   
2  Minimum Wage     7.250000      7.25000     7.250000     7.250000   

   2 ADULTS(1 WORKING) - 0  2 ADULTS(1 WORKING) - 1  2 ADULTS(1 WORKING) - 2  \
0                26.954471                32.088533                37.648038   
1                 8.380000                10.560000                12.740000   
2                 7.250000                 7.250000                 7.250000   

   2 ADULTS(1 WORKING) - 3  2 ADULTS(BOTH WORKING) - 0  \
0                40.880712                   13.477657   
1                14.920000                    4.190000   
2                 7.250000                    7.250000   

   2 ADULTS(BOTH WORKING) - 1  2 ADULTS(BOTH WORKING) - 2  \
0                   17.751381                   22.236004   
1                    5.280000                    6.370000   
2                    7.250000                    7.250000   

   2 ADULTS(BOTH WORKING) - 3           State  Population Estimate 2022  
0                   25.557895  South Carolina                 5282634.0  
1                    7.460000  South Carolina                 5282634.0  
2                    7.250000  South Carolina                 5282634.0

<br/><h5>MIT Living Wage: Typical Expenses by State and Population</h5>

CostType   1 ADULT - 0   1 ADULT - 1  \
0                                 Food   3351.000000   4937.000000   
1                           Child Care      0.000000   5609.889415   
2                              Medical   2957.000000   9182.000000   
3                              Housing   9828.407409  12200.552331   
4                       Transportation   5509.000000   9776.000000   
5                                Civic   2503.000000   4019.000000   
6                                Other   4508.000000   6723.000000   
7   Required annual income after taxes  28779.328545  52570.426477   
8                         Annual taxes   7627.074616  13932.317552   
9  Required annual income before taxes  36406.406425  66502.581846   

    1 ADULT - 2    1 ADULT - 3  2 ADULTS(1 WORKING) - 0  \
0   7417.000000    9838.000000              6143.000000   
1  11219.580293   16829.469708                 0.000000   
2   8969.000000    9278.000000              7086.000000   
3  12200.552331   15917.694809             10451.640438   
4  12709.000000   15012.000000              9776.000000   
5   4965.000000    6483.000000              4019.000000   
6   6150.000000    8948.000000              6723.000000   
7  63753.390054   82430.105953             44320.834205   
8  16896.043510   21845.917305             11746.004772   
9  80649.464619  104276.063840             56066.815028   

   2 ADULTS(1 WORKING) - 1  2 ADULTS(1 WORKING) - 2  2 ADULTS(1 WORKING) - 3  \
0              7645.000000              9856.000000             11999.000000   
1                 0.000000                 0.000000                 0.000000   
2              8969.000000              9278.000000              9067.000000   
3             12200.552331             12200.552331             15917.694809   
4             12709.000000             15012.000000             16304.000000   
5              4965.000000              6483.000000              5153.000000   
6              6150.000000              8948.000000              8655.000000   
7             52761.687250             61901.333720             67219.023661   
8             13982.900844             16405.232944             17814.591408   
9             66744.474960             78306.474960             85033.415583   

   2 ADULTS(BOTH WORKING) - 0  2 ADULTS(BOTH WORKING) - 1  \
0                 6143.000000                 7645.000000   
1                    0.000000                 5609.889415   
2                 7086.000000                 8969.000000   
3                10451.640438                12200.552331   
4                 9776.000000                12709.000000   
5                 4019.000000                 4965.000000   
6                 6723.000000                 6150.000000   
7                44320.834205                58371.576666   
8                11746.004772                15469.598219   
9                56066.815028                73841.181109   

   2 ADULTS(BOTH WORKING) - 2  2 ADULTS(BOTH WORKING) - 3           State  \
0                 9856.000000                11999.000000  South Carolina   
1                11219.580293                16829.469708  South Carolina   
2                 9278.000000                 9067.000000  South Carolina   
3                12200.552331                15917.694809  South Carolina   
4                15012.000000                16304.000000  South Carolina   
5                 6483.000000                 5153.000000  South Carolina   
6                 8948.000000                 8655.000000  South Carolina   
7                73120.914012                84048.493369  South Carolina   
8                19378.660306                22274.621166  South Carolina   
9                92499.464619               106323.271967  South Carolina   

   Population Estimate 2022  
0                 5282634.0  
1                 5282634.0  
2                 5282634.0  
3                 5282634.0  
4                 5282634.0  
5                 5282634.0 

<br/><h5>MIT Living Wage: Occupation Salary by State and Population</h5>

State                                  Occupational Area  \
0   Alabama                     Architecture &amp; Engineering   
1   Alabama   Arts, Design, Entertainment, Sports, &amp; Media   
2   Alabama  Building &amp; Grounds Cleaning &amp; Maintenance   
3   Alabama                Business &amp; Financial Operations   
4   Alabama                     Community &amp; Social Service   
5   Alabama                        Computer &amp; Mathematical   
6   Alabama                      Construction &amp; Extraction   
7   Alabama                 Education, Training, &amp; Library   
8   Alabama                   Farming, Fishing, &amp; Forestry   
9   Alabama             Food Preparation &amp; Serving Related   
10  Alabama           Healthcare Practitioners &amp; Technical   
11  Alabama                                 Healthcare Support   
12  Alabama            Installation, Maintenance, &amp; Repair   
13  Alabama                                              Legal   
14  Alabama               Life, Physical, &amp; Social Science   
15  Alabama                                         Management   
16  Alabama                Office &amp; Administrative Support   
17  Alabama                        Personal Care &amp; Service   
18  Alabama                                         Production   
19  Alabama                                 Protective Service   
20  Alabama                                Sales &amp; Related   
21  Alabama               Transportation &amp; Material Moving   

    Population Estimate 2022  Typical Annual Salary  
0                    5074296                90447.0  
1                    5074296                41698.0  
2                    5074296                26108.0  
3                    5074296                71198.0  
4                    5074296                47059.0  
5                    5074296                86938.0  
6                    5074296                42490.0  
7                    5074296                54260.0  
8                    5074296                32132.0  
9                    5074296                20812.0  
10                   5074296                58080.0  
11                   5074296                26055.0  
12                   5074296                48910.0  
13                   5074296                69240.0  
14                   5074296                64992.0  
15                   5074296               101778.0  
16                   5074296                36829.0  
17                   5074296                23925.0  
18                   5074296                36123.0  
19                   5074296                39975.0  
20                   5074296                28291.0  
21                   5074296                32175.0

## Visuals
### preprocessing

In [40]:
#Data long form
MeltedCosts = pd.melt(StateCostDF, id_vars  = ['State','Population Estimate 2022', 'CostType'], var_name='Household', value_name='Cost')
MeltedCosts['Num Adults in Household'] = MeltedCosts['Household'].apply(lambda x: x.split(' ')[0])
MeltedCosts['Num of working Adults in Household'] = MeltedCosts['Household'].apply(lambda x: 1 if '2 ADULTS(1 WORKING)' in x else 2 if '2 ADULTS(BOTH WORKING)' in x else 1)
MeltedCosts['Num of children in Household'] = MeltedCosts['Household'].apply(lambda x: x.split(' ')[-1])
MeltedCosts.drop(MeltedCosts[MeltedCosts['CostType']=='Required annual income after taxes'].index, inplace = True )
MeltedCosts.drop(MeltedCosts[MeltedCosts['CostType']=='Required annual income before taxes'].index, inplace = True )
MeltedCosts['CostType'] = MeltedCosts['CostType'] + ' Cost'
MeltedCosts.drop('Household', axis = 1, inplace = True)
MeltedCosts.rename(columns={'Cost': 'Amount'}, inplace=True)
MeltedCosts.rename(columns={'CostType': 'Variable'}, inplace=True)
display(MeltedCosts.head())

MeltedWages = pd.melt(StateWageDF, id_vars = ['State','Population Estimate 2022', 'WageType'], var_name='Household', value_name='Earnings')
MeltedWages['Num Adults in Household'] = MeltedWages['Household'].apply(lambda x: x.split(' ')[0])
MeltedWages['Num of working Adults in Household'] = MeltedWages['Household'].apply(lambda x: 1 if '2 ADULTS(1 WORKING)' in x else 2 if '2 ADULTS(BOTH WORKING)' in x else 1)
MeltedWages['Num of children in Household'] = MeltedWages['Household'].apply(lambda x: x.split(' ')[-1])
MeltedWages.drop('Household', axis = 1, inplace = True)
# taking wages to annual
MeltedWages['Earnings'] = MeltedWages['Earnings'] * 2080
#adjusting for dual income
MeltedWages.loc[MeltedWages['Num of working Adults in Household'] == 2, 'Earnings'] *= 2
MeltedWages.rename(columns={'Earnings': 'Amount'}, inplace=True)
MeltedWages.rename(columns={'WageType': 'Variable'}, inplace=True)
display(MeltedWages.head())

StateSalary['Occupational Area']= StateSalary['Occupational Area'].str.replace('&amp;', 'and', regex=False)
display(StateSalary.head())


Parity_merger=RPP[['GeoName','DataValue']].copy()
Parity_merger.rename(columns={'GeoName': 'State','DataValue':'RPP'}, inplace=True)

#merging Parity to MIT
CostParity = pd.merge(Parity_merger, MeltedCosts, left_on = 'State', right_on = 'State', how = 'inner')
display(CostParity.sample(10))
WageParity = pd.merge(Parity_merger, MeltedWages, left_on = 'State', right_on = 'State', how = 'inner')
display(WageParity.sample(10))
OccupationParity = pd.merge(Parity_merger, StateSalary, left_on = 'State', right_on = 'State', how = 'inner')



#standardizing $ by parity
#IVP_Cost = CostParity.rename({'DataValue': 'RPP'}, axis = 'columns')
CostParity["std Costs"] = (CostParity["Amount"] / (CostParity["RPP"]/100)).round()
CostParity.sort_values(by="std Costs", ascending=False, inplace=True)


#IVP_Wage = WageParity.rename({'DataValue':'RPP'}, axis = 'columns')
WageParity["std wages"] = (WageParity["Amount"] / (WageParity["RPP"]/100)).round()
WageParity.sort_values(by="std wages", ascending=False, inplace=True)


#IVP_OCC = OccupationParity.rename({'DataValue':'RPP'}, axis = 'columns')
OccupationParity["std Salaries"] = (OccupationParity["Typical Annual Salary"] / (OccupationParity["RPP"]/100)).round()
OccupationParity.sort_values(by="std Salaries", ascending=False, inplace=True)



#Total Household expenditures
IVP_Cost_Total = CostParity.groupby(['State',"Population Estimate 2022",'Num Adults in Household', 'Num of working Adults in Household','Num of children in Household' ]).agg({'std Costs': 'sum'}).reset_index()
#merge total expenditures with Wage and compare via divison across all households
WageVCost = pd.merge(WageParity, IVP_Cost_Total, left_on = ['State','Num Adults in Household', 'Num of working Adults in Household','Num of children in Household'], right_on = ['State','Num Adults in Household', 'Num of working Adults in Household','Num of children in Household' ], how = 'inner')
#WageVCost = pd.concat([WageParity, IVP_Cost_Total,])
WageVCost['IncomeVExpenses'] = (WageVCost['std wages'] - WageVCost['std Costs'])/(WageVCost['std wages'] + WageVCost['std Costs'])


#compare occupation with wage and cost data. applying filter to not make huge table
#pick occupation
occupations = [
    'Management', 'Computer and Mathematical',
    'Architecture and Engineering', 'Legal',
    'Healthcare Practitioners and Technical',
    'Life, Physical, and Social Science',
    'Business and Financial Operations', 
    'Construction and Extraction',
    'Arts, Design, Entertainment, Sports, and Media',
    'Education, Training, and Library',
    'Community and Social Service',
    'Installation, Maintenance, and Repair',
    'Production', 'Protective Service',
    'Transportation and Material Moving',
    'Farming, Fishing, and Forestry',
    'Office and Administrative Support',
    'Healthcare Support','Sales and Related',
    'Building and Grounds Cleaning and Maintenance',
    'Personal Care and Service',
    'Food Preparation and Serving Related']

#Occupation = 'Computer and Mathematical'
#WageVCost2 = WageVCost[WageVCost["Num of working Adults in Household"]!=2]
display(WageVCost)
WageVCostVOCC= pd.merge(WageVCost, OccupationParity, left_on = ['State'], right_on = ['State'], how = 'inner')
display(WageVCostVOCC)

WageVCostVOCC= WageVCostVOCC[['State', 'Variable', 'Num Adults in Household', 'Num of working Adults in Household','Num of children in Household', 'Occupational Area', 'std wages', 'std Costs', 'std Salaries' , 'Population Estimate 2022'   ]]
WageVCostVOCC['HouseHold'] = 'Adults: ' + WageVCostVOCC['Num Adults in Household'].astype(str)  \
    + np.where(WageVCostVOCC['Num of working Adults in Household'] == 1, ', Sole Income, ', ', Dual Income, ') \
    + WageVCostVOCC['Num of children in Household'].astype(str) + ' kids'
WageVCostVOCC.drop(['Num Adults in Household', 'Num of working Adults in Household','Num of children in Household'], axis= 1, inplace=True)

WageVCostVOCC.sample(30)

State  Population Estimate 2022             Variable       Amount  \
0  South Carolina                 5282634.0            Food Cost  3351.000000   
1  South Carolina                 5282634.0      Child Care Cost     0.000000   
2  South Carolina                 5282634.0         Medical Cost  2957.000000   
3  South Carolina                 5282634.0         Housing Cost  9828.407409   
4  South Carolina                 5282634.0  Transportation Cost  5509.000000   

  Num Adults in Household  Num of working Adults in Household  \
0                       1                                   1   
1                       1                                   1   
2                       1                                   1   
3                       1                                   1   
4                       1                                   1   

  Num of children in Household  
0                            0  
1                            0  
2                            0  
3                            0  
4                            0

State  Population Estimate 2022      Variable        Amount  \
0  South Carolina                 5282634.0   Living Wage  36406.663852   
1  South Carolina                 5282634.0  Poverty Wage  12875.200000   
2  South Carolina                 5282634.0  Minimum Wage  15080.000000   
3       Louisiana                 4575512.0   Living Wage  33624.359178   
4       Louisiana                 4575512.0  Poverty Wage  12875.200000   

  Num Adults in Household  Num of working Adults in Household  \
0                       1                                   1   
1                       1                                   1   
2                       1                                   1   
3                       1                                   1   
4                       1                                   1   

  Num of children in Household  
0                            0  
1                            0  
2                            0  
3                            0  
4                            0

State                               Occupational Area  \
0  Alabama                    Architecture and Engineering   
1  Alabama  Arts, Design, Entertainment, Sports, and Media   
2  Alabama   Building and Grounds Cleaning and Maintenance   
3  Alabama               Business and Financial Operations   
4  Alabama                    Community and Social Service   

   Population Estimate 2022  Typical Annual Salary  
0                   5074296                90447.0  
1                   5074296                41698.0  
2                   5074296                26108.0  
3                   5074296                71198.0  
4                   5074296                47059.0

State      RPP  Population Estimate 2022             Variable  \
3411        Oklahoma   88.771                 4019800.0         Housing Cost   
1575        Kentucky   89.356                 4512310.0    Annual taxes Cost   
2032        Michigan   93.428                10034113.0            Food Cost   
1806           Maine  100.839                 1280610.0           Other Cost   
3053        New York  107.599                19677151.0           Civic Cost   
3430        Oklahoma   88.771                 4019800.0           Other Cost   
3712    Rhode Island  104.700                 1043374.0            Food Cost   
3156  North Carolina   94.204                10698973.0  Transportation Cost   
145           Alaska  101.989                  686305.0      Child Care Cost   
2279     Mississippi   87.328                 2940057.0    Annual taxes Cost   

            Amount Num Adults in Household  \
3411  10933.935893                       2   
1575   9515.918808                       2   
2032   7577.000000                       1   
1806   7197.000000                       2   
3053   6361.000000                       2   
3430   6723.000000                       2   
3712   7133.000000                       2   
3156  15012.000000                       2   
145       0.000000                       2   
2279   9726.395709                       2   

      Num of working Adults in Household Num of children in Household  
3411                                   1                            2  
1575                                   1                            0  
2032                                   1                            2  
1806                                   2                            1  
3053                                   2                            1  
3430                                   2                            0  
3712                                   2                            0  
3156                                   2                            2  
145                                    1                            2  
2279                                   2                            0

State      RPP  Population Estimate 2022      Variable  \
535          Iowa   88.422                 3200517.0  Poverty Wage   
1259         Ohio   91.450                11756058.0  Minimum Wage   
1003       Nevada   96.383                 3177772.0  Poverty Wage   
1603      Vermont  101.096                  639575.0  Poverty Wage   
1534        Texas   97.512                30029572.0  Poverty Wage   
321       Florida  102.144                22244823.0   Living Wage   
1140     New York  107.599                19677151.0   Living Wage   
1503    Tennessee   91.797                 7051339.0   Living Wage   
18        Alabama   87.776                 5074296.0   Living Wage   
233   Connecticut  106.412                 3693514.0  Minimum Wage   

             Amount Num Adults in Household  \
535    26499.200000                       2   
1259   38688.000000                       2   
1003   26499.200000                       2   
1603   26499.200000                       2   
1534   31033.600000                       2   
321   116793.331434                       2   
1140   64713.089673                       2   
1503   65898.200904                       2   
18     72874.169363                       2   
233    29120.000000                       2   

      Num of working Adults in Household Num of children in Household  
535                                    2                            2  
1259                                   2                            3  
1003                                   2                            2  
1603                                   1                            2  
1534                                   1                            3  
321                                    2                            3  
1140                                   2                            0  
1503                                   2                            1  
18                                     1                            2  
233                                    1                            1

State      RPP  Population Estimate 2022_x      Variable  \
0     Massachusetts  109.393                   6981974.0   Living Wage   
1     Massachusetts  109.393                   6981974.0   Living Wage   
2          Michigan   93.428                  10034113.0   Living Wage   
3          Michigan   93.428                  10034113.0   Living Wage   
4        California  112.470                  39029342.0   Living Wage   
...             ...      ...                         ...           ...   
1795  New Hampshire  107.644                   1395231.0  Poverty Wage   
1796     New Jersey  108.757                   9261699.0  Poverty Wage   
1797  Massachusetts  109.393                   6981974.0  Poverty Wage   
1798     Washington  109.849                   7785786.0  Poverty Wage   
1799     California  112.470                  39029342.0  Poverty Wage   

             Amount Num Adults in Household  \
0     160432.269695                       2   
1     158893.566746                       1   
2     133662.527570                       2   
3     131971.974070                       1   
4     155857.081930                       2   
...             ...                     ...   
1795   12875.200000                       1   
1796   12875.200000                       1   
1797   12875.200000                       1   
1798   12875.200000                       1   
1799   12875.200000                       1   

      Num of working Adults in Household Num of children in Household  \
0                                      2                            3   
1                                      1                            3   
2                                      2                            3   
3                                      1                            3   
4                                      2                            3   
...                                  ...                          ...   
1795                                   1                            0   
1796                                   1                            0   
1797                                   1                            0   
1798                                   1                            0   
1799                                   1                            0   

      std wages  Population Estimate 2022_y  std Costs  IncomeVExpenses  
0      146657.0                   6981974.0   146544.0         0.000385  
1      145250.0                   6981974.0   145139.0         0.000382  
2      143065.0                  10034113.0   142933.0         0.000462  
3      141255.0                  10034113.0   141125.0         0.000460  
4      138577.0                  39029342.0   138466.0         0.000401  
...         ...                         ...        ...              ...  
1795    11961.0                   1395231.0    33356.0        -0.472119  
1796    11839.0                   9261699.0    38991.0        -0.534173  
1797    11770.0                   6981974.0    41455.0        -0.557727  
1798    11721.0                   7785786.0    34962.0        -0.497847  
1799    11448.0                  39029342.0    40433.0        -0.558682  

[1800 rows x 12 columns]

State    RPP_x  Population Estimate 2022_x      Variable  \
0      Massachusetts  109.393                   6981974.0   Living Wage   
1      Massachusetts  109.393                   6981974.0   Living Wage   
2      Massachusetts  109.393                   6981974.0   Living Wage   
3      Massachusetts  109.393                   6981974.0   Living Wage   
4      Massachusetts  109.393                   6981974.0   Living Wage   
...              ...      ...                         ...           ...   
39595     California  112.470                  39029342.0  Poverty Wage   
39596     California  112.470                  39029342.0  Poverty Wage   
39597     California  112.470                  39029342.0  Poverty Wage   
39598     California  112.470                  39029342.0  Poverty Wage   
39599     California  112.470                  39029342.0  Poverty Wage   

              Amount Num Adults in Household  \
0      160432.269695                       2   
1      160432.269695                       2   
2      160432.269695                       2   
3      160432.269695                       2   
4      160432.269695                       2   
...              ...                     ...   
39595   12875.200000                       1   
39596   12875.200000                       1   
39597   12875.200000                       1   
39598   12875.200000                       1   
39599   12875.200000                       1   

       Num of working Adults in Household Num of children in Household  \
0                                       2                            3   
1                                       2                            3   
2                                       2                            3   
3                                       2                            3   
4                                       2                            3   
...                                   ...                          ...   
39595                                   1                            0   
39596                                   1                            0   
39597                                   1                            0   
39598                                   1                            0   
39599                                   1                            0   

       std wages  Population Estimate 2022_y  std Costs  IncomeVExpenses  \
0       146657.0                   6981974.0   146544.0         0.000385   
1       146657.0                   6981974.0   146544.0         0.000385   
2       146657.0                   6981974.0   146544.0         0.000385   
3       146657.0                   6981974.0   146544.0         0.000385   
4       146657.0                   6981974.0   146544.0         0.000385   
...          ...                         ...        ...              ...   
39595    11448.0                  39029342.0    40433.0        -0.558682   
39596    11448.0                  39029342.0    40433.0        -0.558682   
39597    11448.0                  39029342.0    40433.0        -0.558682   
39598    11448.0                  39029342.0    40433.0        -0.558682   
39599    11448.0                  39029342.0    40433.0        -0.558682   

         RPP_y                              Occupational Area  \
0      109.393                                     Management   
1      109.393                                          Legal   
2      109.393                      Computer and Mathematical   
3      109.393                   Architecture and Engineering   
4      109.393         Healthcare Practitioners and Technical   
...        ...                                            ...   
39595  112.470  Building and Grounds Cleaning and Maintenance   
39596  112.470                      Personal Care and Service   
39597  112.470                             Healthcare Support   
39598  112.470           Food Preparation and Serving Related   
39599  112.470      

State      Variable                       Occupational Area  \
10020            Iowa   Living Wage        Education, Training, and Library   
27987         Georgia  Poverty Wage                                   Legal   
11058       Wisconsin   Living Wage       Office and Administrative Support   
35303        Kentucky  Minimum Wage      Transportation and Material Moving   
29273           Maine  Poverty Wage                              Production   
18522  North Carolina  Minimum Wage               Personal Care and Service   
14372        Nebraska  Minimum Wage      Life, Physical, and Social Science   
27965            Utah  Poverty Wage            Architecture and Engineering   
30940   New Hampshire  Poverty Wage                      Protective Service   
14126         Montana  Minimum Wage  Healthcare Practitioners and Technical   
11098  North Carolina   Living Wage            Community and Social Service   
3348          Montana   Living Wage       Business and Financial Operations   
10848            Utah   Living Wage                                   Legal   
30126          Alaska  Minimum Wage   Installation, Maintenance, and Repair   
22249     Connecticut  Minimum Wage        Education, Training, and Library   
14547   West Virginia  Minimum Wage      Life, Physical, and Social Science   
26426          Kansas  Poverty Wage       Business and Financial Operations   
39320        Virginia  Poverty Wage  Healthcare Practitioners and Technical   
32499        Missouri  Poverty Wage      Life, Physical, and Social Science   
34577         Florida  Poverty Wage      Transportation and Material Moving   
24114         Vermont  Minimum Wage            Architecture and Engineering   
25992        Illinois  Minimum Wage   Installation, Maintenance, and Repair   
27663    South Dakota  Minimum Wage        Education, Training, and Library   
24647        Arkansas  Poverty Wage        Education, Training, and Library   
91         California   Living Wage            Architecture and Engineering   
38113      California  Poverty Wage             Construction and Extraction   
35047        Oklahoma  Minimum Wage            Architecture and Engineering   
20043        Nebraska  Poverty Wage               Computer and Mathematical   
4352         Delaware   Living Wage                       Sales and Related   
35667       Louisiana  Minimum Wage       Business and Financial Operations   

       std wages  std Costs  std Salaries  Population Estimate 2022  \
10020    60436.0    60300.0       54987.0                   3200517   
27987    22920.0    85594.0       82379.0                  10904613   
11058    57132.0    56995.0       44650.0                   5892539   
35303    16876.0    80166.0       38894.0                   4512310   
29273    21782.0    68394.0       43049.0                   1280610   
18522    32016.0   105290.0       27669.0                  10698973   
14372    41690.0   127236.0       69986.0                   1967923   
27965    23250.0    78679.0       82081.0                   3380800   
30940    20405.0    82128.0       48468.0                   1395231   
14126    42399.0    84088.0       79244.0                   1122867   
11098    57121.0    56990.0       53066.0                  10698973   
3348     96273.0    96140.0       70827.0                   1122867   
10848    57541.0    57415.0       83021.0                   3380800   
30126    21088.0    80939.0       64805.0                    686305   
22249    27365.0    79596.0       63740.0                   3693514   
14547    40787.0    57330.0       70282.0                   3550312   
26426    24416.0    73202.0       75646.0                   2937150   
39320    12606.0    39499.0       71144.0                   8459727   
32499    19129.0    58539.0       71350.0                   5891379   
34577    17065.0    53391.0       32327.0                  22244823   
24114    25821.0    36484.0       75665.0                    639575   
2599

In [99]:
familyCosts = CostParity.copy()
familyCosts['HouseHold'] = 'Adults: ' + familyCosts['Num Adults in Household'].astype(str)  \
    + np.where(familyCosts['Num of working Adults in Household'] == 1, ', Sole Income, ', ', Dual Income, ') \
    + familyCosts['Num of children in Household'].astype(str) + ' kids'
familyCosts.drop(['Num Adults in Household', 'Num of working Adults in Household','Num of children in Household'], axis= 1, inplace=True)


def altHeatMap(df,ChartTitle, X, X_Title, Y, Y_Title, Color, LegendTitle ):
    heatmap = alt.Chart(df).mark_rect().encode(
    x=alt.X(X + ':N', title=X_Title,
            sort=alt.EncodingSortField(field=Color, order='ascending')),
    y=alt.Y(Y +':N', title=Y_Title,
            sort=alt.EncodingSortField(field=Color, order='descending')),
    color=alt.Color(Color +':Q', title=LegendTitle, scale = alt.Scale(scheme='viridis'))
    ).properties(
        title=ChartTitle,
        width=600,
        height=400
    )

   
    return heatmap

PopVLivingVsalary = WageVCostVOCC[WageVCostVOCC['Variable']=="Living Wage" ]
HM_1 = altHeatMap(PopVLivingVsalary,'Heatmap of Expected Earnings vs. Occupation by State',
           'State', 'State', 'Occupational Area', 'Occupation', 'std Salaries', 'Salary')
HM_2 = altHeatMap(PopVLivingVsalary,'Estimated Household Living Wage Parity Adj',
           'State', 'State', 'HouseHold', 'House Hold', 'std wages', 'Annual Estimate')
HM_3 = altHeatMap(PopVLivingVsalary,'Estimated Household Costs Parity Adj',
           'State', 'State', 'HouseHold', 'House Hold', 'std Costs', 'Annual Estimate')

PopVLivingVsalary = WageVCostVOCC[WageVCostVOCC['Variable']=="Poverty Wage" ]
HM_4 = altHeatMap(PopVLivingVsalary,'Estimated Household Poverty Wage Parity Adj',
           'State', 'State', 'HouseHold', 'House Hold', 'std wages', 'Annual Estimate')

PopVLivingVsalary = WageVCostVOCC[WageVCostVOCC['Variable']=="Minimum Wage" ]
HM_5 = altHeatMap(PopVLivingVsalary,'Estimated Household Minimum Wage Parity Adj',
           'State', 'State', 'HouseHold', 'House Hold', 'std wages', 'Annual Estimate')

HM_6 = altHeatMap(familyCosts,'Estimated Household Expenses Parity Adj',
           'State', 'State', 'Variable', 'Expenses', 'Amount', 'Annual Estimate')


#charts = alt.vconcat(HM_1, HM_2).resolve_scale(y='independent')
#charts
display(HM_1)

display(((HM_2|HM_5).resolve_scale(y='independent', color='independent')
    & (HM_3|HM_4).resolve_scale(y='independent', color='independent')))

display(HM_6)


alt.Chart(...)

alt.VConcatChart(...)

alt.Chart(...)

### Chloropleth maps

In [ ]:
states.plot()

<Axes: >